## Downsampling original csv input for futher pre-processing and efficient model training ##

In [1]:
import pandas as pd
import numpy as np

#efficiently reading large csv dataset
dtypes = {
    "event_type": "category",
    "product_id": "int32",
    "category_id": "float32",
    "category_code": "category",
    "brand": "category",
    "price": "float32",
    "user_id": "int32",
    "user_session": "category"
}

df = pd.read_csv("2019-Oct.csv", parse_dates=["event_time"], dtype=dtypes)

In [2]:
#droppings rows missing key identifiers
df.dropna(subset=["brand", "category_code", "user_session"], inplace=True)

In [3]:
#deriving time features without overloading memory
df["date"] = df["event_time"].dt.date
df["hour"] = df["event_time"].dt.hour.astype("int8")
df["day_of_week"] = df["event_time"].dt.day_name().astype("category")

In [4]:
#downsampling ‘view’ events to ~2M rows for more efficient processing
view = df[df["event_type"] == "view"]
cart = df[df["event_type"] == "cart"]
purchase = df[df["event_type"] == "purchase"]

In [5]:
#continuing with downsampling operation
target_view_count = 2_000_000
frac_keep = min(1.0, target_view_count / len(view))
df_reduced = pd.concat([
    view.sample(frac=frac_keep, random_state=42),
    cart,
    purchase
], ignore_index=True)

In [6]:
print(f"Final Dataset has {len(df_reduced):,} rows")

Final Dataset has 3,173,502 rows


In [56]:
df_reduced["price"] = pd.to_numeric(df_reduced["price"], downcast="float")
#df_reduced.to_parquet("ecommerce_reduced.parquet", index=False)
#print("ecommerce_reduced.parquet created efficiently.")

In [15]:
df_reduced.head(5)

event_time event_type  product_id   category_id  \
0 2019-10-10 18:01:42+00:00       view     3700733  2.053014e+18   
1 2019-10-13 14:19:44+00:00       view     1005160  2.053014e+18   
2 2019-10-25 22:41:41+00:00       view     1005105  2.053014e+18   
3 2019-10-13 10:31:07+00:00       view     4802401  2.053014e+18   
4 2019-10-23 12:23:13+00:00       view     1004739  2.053014e+18   

                   category_code    brand        price    user_id  \
0  appliances.environment.vacuum  philips   411.829987  514928871   
1         electronics.smartphone   xiaomi   230.789993  518681649   
2         electronics.smartphone    apple  1379.439941  564203557   
3    electronics.audio.headphone  samsung    43.869999  513058283   
4         electronics.smartphone   xiaomi   189.970001  527362968   

                           user_session        date  hour day_of_week  
0  8710f56e-9495-44c8-9d8e-8075ad147f9f  2019-10-10    18    Thursday  
1  f090e748-2e1c-48a1-a001-e6b3af1be953  2019-10-13    14      Sunday  
2  cc293954-db2f-45ff-b33a-e731e5439af5  2019-10-25    22      Friday  
3  8b9f2b93-dfa6-4adf-972c-576bf122e929  2019-10-13    10      Sunday  
4  2ce6dc35-b02e-4afe-a55a-eec1db5c498e  2019-10-23    12   Wednesday

## Creating Lightweight Aggregations for plotly dash app efficient deployment ##

#### This portion of the analysis serves to create the precursor files or theorized pipelines to feed the dash app showing insightful metric about a given website given ecommerce behavior data ####

In [17]:
import pandas as pd
import numpy as np
import gc

df = pd.read_parquet("ecommerce_reduced.parquet")

In [57]:
df = df_reduced

In [19]:
#creating several parquets for app dash
# keeping memory usage light — utilizing observed=True and category groupbys

daily = (
    df.groupby(["date", "event_type"], observed=True)
      .size()
      .reset_index(name="count")
)
daily.to_parquet("daily_events.parquet", index=False)

hourly = (
    df.groupby(["hour", "event_type"], observed=True)
      .size()
      .reset_index(name="count")
)
hourly.to_parquet("hourly_events.parquet", index=False)

dow = (
    df.groupby(["day_of_week", "event_type"], observed=True)
      .size()
      .reset_index(name="count")
)
dow["day_of_week"] = pd.Categorical(
    dow["day_of_week"],
    categories=["Monday","Tuesday","Wednesday","Thursday","Friday","Saturday","Sunday"],
    ordered=True
)
dow.to_parquet("dow_events.parquet", index=False)

price_summary = (
    df.groupby("event_type", observed=True)["price"]
      .agg(["mean", "median", "std", "min", "max", "count"])
      .reset_index()
)
price_summary.to_parquet("price_summary.parquet", index=False)

funnel = (
    df.groupby("event_type", observed=True)["user_session"]
      .nunique()
      .reset_index(name="unique_sessions")
      .sort_values("unique_sessions", ascending=False)
)
funnel.to_parquet("funnel_summary.parquet", index=False)

In [20]:
# defining brand & category purchases
purchases = df.loc[df["event_type"] == "purchase"]
purchases.groupby("brand", observed=True).size().nlargest(10).reset_index(name="purchase_count").to_parquet("top_brands.parquet", index=False)
purchases.groupby("category_code", observed=True).size().nlargest(10).reset_index(name="purchase_count").to_parquet("top_categories.parquet", index=False)

In [21]:
#defining sessions & histograms
sess_stats = (
    df.groupby("user_session", observed=True)["event_type"]
      .count()
      .reset_index(name="event_count")
)
hist, bins = np.histogram(sess_stats["event_count"], bins=50)
pd.DataFrame({"bin_left": bins[:-1], "bin_right": bins[1:], "count": hist}).to_parquet("session_histogram.parquet", index=False)

In [62]:
# taking a random 50k sample dropping user_session for compactness
session_stats_sample = (
    sess_stats
    .sample(n=50_000, random_state=42)
    .drop(columns=["user_session"])
)
session_stats_sample.to_parquet("session_stats_sample.parquet", index=False)
print("session_stats_sample.parquet created.")

# Take a 2% random sample of price and event_type for visualization
price_sample = (
    df.sample(frac=0.02, random_state=42)[["price", "event_type"]]
)
price_sample.to_parquet("price_sample.parquet", index=False)
print("price_sample.parquet created.")

session_stats_sample.parquet created.
price_sample.parquet created.


In [22]:
del df, purchases, sess_stats
gc.collect()
print("descriptive parquet files created.")

descriptive parquet files created.


In [ ]:
## beginning feature engineering & further pre-processing in preparatin to model training

In [63]:
import pandas as pd
import numpy as np
import gc
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler, OneHotEncoder
from sklearn.compose import ColumnTransformer
from sklearn.pipeline import Pipeline
from sklearn.linear_model import LogisticRegression
import joblib

#preparing for logistic regrassion model training using,
#df = pd.read_parquet("ecommerce_reduced.parquet")
#or df_reduced

df = df_reduced
df = df.drop_duplicates()

In [27]:
# computing session-level aggregates incrementally to avoid holding full wide table
df["is_purchase"] = (df["event_type"] == "purchase").astype("int8")
sess_label = df.groupby("user_session", observed=True)["is_purchase"].max().rename("purchase_flag")

In [64]:
# defining event counts per session
evt_counts = (
    df.groupby(["user_session", "event_type"], observed=True)
      .size()
      .unstack(fill_value=0)
      .add_prefix("evt_")
)
evt_counts["evt_total"] = evt_counts.sum(axis=1)

In [65]:
# defining price statistics
price_stats = df.groupby("user_session", observed=True)["price"].agg(["mean", "max", "min"])
price_stats.columns = ["price_mean", "price_max", "price_min"]

In [30]:
richness = df.groupby("user_session", observed=True).agg(
    n_products=("product_id","nunique"),
    n_brands=("brand","nunique"),
    n_categories=("category_code","nunique")
)

In [66]:
# defining the dominant hour & day of the week
dom_time = df.groupby("user_session", observed=True).agg(
    dom_hour=("hour", lambda s: s.mode().iloc[0]),
    dom_dow=("day_of_week", lambda s: s.mode().iloc[0])
)

In [33]:
data = evt_counts.join([price_stats, richness, dom_time, sess_label], how="left")

# fill only numeric NaNs handling categoricals separately
num_cols = data.select_dtypes(include=["number"]).columns
data[num_cols] = data[num_cols].fillna(0)

cat_cols = data.select_dtypes(include=["category"]).columns
for c in cat_cols:
    if data[c].isna().any():
        mode_val = data[c].mode(dropna=True)
        if not mode_val.empty:
            data[c] = data[c].fillna(mode_val[0])

del df, evt_counts, price_stats, richness, dom_time, sess_label
gc.collect()

1731

In [34]:
data.head(5)

evt_cart  evt_purchase  evt_view  \
user_session                                                             
00399d10-e0d3-4d17-9760-30c42851777c         0             0         1   
0061c89b-caa1-420c-a8c2-2a7f03457bef         0             0         1   
0083c34e-900e-4529-81e0-8001c41db3b5         0             0         1   
009074dd-dda3-4032-9e3e-b45fed5fa579         0             0         1   
00a0f1ab-3c62-4c63-8ab7-6db822400230         0             0         2   

                                      evt_total   price_mean    price_max  \
user_session                                                                
00399d10-e0d3-4d17-9760-30c42851777c          1  1012.190002  1012.190002   
0061c89b-caa1-420c-a8c2-2a7f03457bef          1   308.859985   308.859985   
0083c34e-900e-4529-81e0-8001c41db3b5          1   118.150002   118.150002   
009074dd-dda3-4032-9e3e-b45fed5fa579          1   124.449997   124.449997   
00a0f1ab-3c62-4c63-8ab7-6db822400230          2   333.614990   488.820007   

                                        price_min  n_products  n_brands  \
user_session                                                              
00399d10-e0d3-4d17-9760-30c42851777c  1012.190002           1         1   
0061c89b-caa1-420c-a8c2-2a7f03457bef   308.859985           1         1   
0083c34e-900e-4529-81e0-8001c41db3b5   118.150002           1         1   
009074dd-dda3-4032-9e3e-b45fed5fa579   124.449997           1         1   
00a0f1ab-3c62-4c63-8ab7-6db822400230   178.410004           2         2   

                                      n_categories  dom_hour  dom_dow  \
user_session                                                            
00399d10-e0d3-4d17-9760-30c42851777c             1         3  Tuesday   
0061c89b-caa1-420c-a8c2-2a7f03457bef             1         2  Tuesday   
0083c34e-900e-4529-81e0-8001c41db3b5             1         3  Tuesday   
009074dd-dda3-4032-9e3e-b45fed5fa579             1         2  Tuesday   
00a0f1ab-3c62-4c63-8ab7-6db822400230             2         3  Tuesday   

                                      purchase_flag  
user_session                                         
00399d10-e0d3-4d17-9760-30c42851777c              0  
0061c89b-caa1-420c-a8c2-2a7f03457bef              0  
0083c34e-900e-4529-81e0-8001c41db3b5              0  
009074dd-dda3-4032-9e3e-b45fed5fa579              0  
00a0f1ab-3c62-4c63-8ab7-6db822400230              0

#### continuing with data modeling ####

In [35]:
# drop evt_purchase and evt_total to avoid label leakage
safe_data = data.drop(columns=["evt_purchase", "evt_total"], errors="ignore")

y = safe_data["purchase_flag"].astype("int8")
X = safe_data.drop(columns=["purchase_flag"])

In [37]:
# defining numeric features list
numeric_features = [
    "evt_cart", "evt_view",
    "price_mean", "price_max", "price_min",
    "n_products", "n_brands", "n_categories",
    "dom_hour"
]

In [38]:
# defining categorical features
categorical_features = ["dom_dow"]

In [39]:
# defining test train split
X_train, X_valid, y_train, y_valid = train_test_split(
    X, y, test_size=0.2, random_state=42, stratify=y
)

In [40]:
print(f"Training: {X_train.shape}, Validation: {X_valid.shape}")
print(f"Positive rate in train: {y_train.mean():.4f}")

Training: (1456544, 10), Validation: (364137, 10)
Positive rate in train: 0.2172


In [41]:
# preprocessing numeric and categorical features separately
preprocess = ColumnTransformer([
    ("num", StandardScaler(), numeric_features),
    ("cat", OneHotEncoder(handle_unknown="ignore", sparse_output=False), categorical_features)
])


In [42]:
# fitting the model
X_train_prep = preprocess.fit_transform(X_train)
X_valid_prep = preprocess.transform(X_valid)

In [44]:
# initialize the Logistic Regression model
# Parameter used,
# solver='saga': algorithm to use for optimization. great for large datasets and handles L1/L2 regularization
# max_iter=300: max. # of iterations taken for the solvers to converge
# n_jobs=-1: Uses all available CPU cores for computation to speed up training
# class_weight='balanced': automatically adjusts weights inversely proportional to class frequencies in the input data 
# useful for handling any possible left classes after downsampling
model = LogisticRegression(solver='saga', max_iter=300, n_jobs=-1, class_weight='balanced')

# Fit the model to the training data
# X_train_prep: Preprocessed features of the training set
# y_train: Target variable (labels) of the training set
model.fit(X_train_prep, y_train)

LogisticRegression(class_weight='balanced', max_iter=300, n_jobs=-1,
                   solver='saga')

In [46]:
from sklearn.metrics import roc_auc_score, average_precision_score, classification_report
# Predicted probabilities for the positive class
p_valid = model.predict_proba(X_valid_prep)[:, 1]

# Binary predictions at 0.5 threshold
y_pred = (p_valid >= 0.5).astype(int)

# Evaluation metrics
roc = roc_auc_score(y_valid, p_valid)
pr  = average_precision_score(y_valid, p_valid)

print(f"ROC AUC: {roc:.4f} | PR AUC: {pr:.4f}\n")
print(classification_report(y_valid, y_pred, digits=3))


ROC AUC: 0.8662 | PR AUC: 0.5919

              precision    recall  f1-score   support

           0      0.944     0.884     0.913    285038
           1      0.659     0.811     0.727     79099

    accuracy                          0.868    364137
   macro avg      0.802     0.847     0.820    364137
weighted avg      0.882     0.868     0.873    364137



In [49]:
# confirm proportion of buyer (1) vs non-buyer (0) sessions
y_valid.value_counts(normalize=True).rename({0: "Non-purchase", 1: "Purchase"})


purchase_flag
Non-purchase    0.782777
Purchase        0.217223
Name: proportion, dtype: float64

#### model insights and justification for usage in dash app ####
About 22% of all sessions ended in a purchase, so the data is somewhat imbalanced, which is to be expected since most sessions don’t result in a purchase. Leaving the imbalance in place allows the model to learn and reflect that real behavior in its predictions.
Even with this imbalance, the logistic regression model performed well, achieving a ROC AUC of 0.87 and a PR AUC of 0.59 on the validation set.
This means it separates buyer sessions from non-buyers effectively while maintaining solid precision and recall (81% recall, 66% precision).
Because the model already uses class weighting and the goal is to visualize conversion patterns rather than make operational decisions, resampling isn’t needed. Overall, the model’s performance is strong, stable, and realistic, making it well-suited for powering the heatmap and feature importance visualizations in the Dash app.

### next the model is used to generate an interactive viz on the likelihood of purchases per time and day of the week, given the dash app the ability to enhance the user's marketing strategy ###

In [51]:
# generating heatmap_data.parquet

# building probability DataFrame with temporal features
proba_df = X_valid[["dom_dow", "dom_hour"]].copy()
proba_df["pred_prob"] = p_valid

# average predicted probability by day of week and hour
heatmap_data = (
    proba_df.groupby(["dom_dow", "dom_hour"], observed=True)["pred_prob"]
            .mean()
            .reset_index()
)

In [52]:
# order weekdays for consistent visualization
day_order = ["Sunday", "Monday", "Tuesday", "Wednesday", "Thursday", "Friday", "Saturday"]
heatmap_data["dom_dow"] = pd.Categorical(heatmap_data["dom_dow"], categories=day_order, ordered=True)
heatmap_data = heatmap_data.sort_values(["dom_dow", "dom_hour"])

# Save as parquet
heatmap_data.to_parquet("heatmap_data.parquet", index=False)
print("heatmap_data.parquet created successfully.")


heatmap_data.parquet created successfully.


In [53]:
# generating feature_importance_data.parquet
# extract feature names and coefficients
feature_names = preprocess.get_feature_names_out()
feature_importance = pd.DataFrame({
    "Feature": feature_names,
    "Coefficient": model.coef_[0]
}).sort_values("Coefficient", ascending=False).reset_index(drop=True)

# saving as parquet
feature_importance.to_parquet("feature_importance_data.parquet", index=False)
print("feature_importance_data.parquet created successfully.")

feature_importance_data.parquet created successfully.


In [67]:
#gc.collect()

## Clutering Model

In [13]:
import pandas as pd
import plotly.express as px
from sklearn.preprocessing import StandardScaler, OneHotEncoder
from sklearn.compose import ColumnTransformer
from sklearn.pipeline import Pipeline
from sklearn.cluster import KMeans
from sklearn.metrics import silhouette_score
from sklearn.decomposition import PCA
from plotly.subplots import make_subplots
import plotly.graph_objects as go

In [26]:
df = df_reduced
# df = pd.read_parquet('ecommerce_reduced.parquet')
df.head(5)

event_time event_type  product_id          category_id  \
0 2019-10-10 18:01:42+00:00       view     3700733  2053013565983425517   
1 2019-10-13 14:19:44+00:00       view     1005160  2053013555631882655   
2 2019-10-25 22:41:41+00:00       view     1005105  2053013555631882655   
3 2019-10-13 10:31:07+00:00       view     4802401  2053013554658804075   
4 2019-10-23 12:23:13+00:00       view     1004739  2053013555631882655   

                   category_code    brand    price    user_id  \
0  appliances.environment.vacuum  philips   411.83  514928871   
1         electronics.smartphone   xiaomi   230.79  518681649   
2         electronics.smartphone    apple  1379.44  564203557   
3    electronics.audio.headphone  samsung    43.87  513058283   
4         electronics.smartphone   xiaomi   189.97  527362968   

                           user_session        date  hour day_of_week  
0  8710f56e-9495-44c8-9d8e-8075ad147f9f  2019-10-10    18    Thursday  
1  f090e748-2e1c-48a1-a001-e6b3af1be953  2019-10-13    14      Sunday  
2  cc293954-db2f-45ff-b33a-e731e5439af5  2019-10-25    22      Friday  
3  8b9f2b93-dfa6-4adf-972c-576bf122e929  2019-10-13    10      Sunday  
4  2ce6dc35-b02e-4afe-a55a-eec1db5c498e  2019-10-23    12   Wednesday

In [6]:
# more feature engineering for clustering, user level
user_df = df.groupby('user_id').agg(
    num_events=('event_type', 'count'),
    num_views=('event_type', lambda x: (x == 'view').sum()),
    num_cart=('event_type', lambda x: (x == 'cart').sum()),
    num_purchases=('event_type', lambda x: (x == 'purchase').sum()),
    avg_price_viewed=('price', 'mean'),
    unique_categories=('category_code', pd.Series.nunique),
    unique_brands=('brand', pd.Series.nunique),
    last_event=('event_time', 'max'),
    first_event=('event_time', 'min'),
    avg_hour=('hour', 'mean'),
).reset_index()

user_df['conversion_rate'] = user_df['num_purchases'] / user_df['num_views'].replace(0, 1) 
user_df['recency_days'] = (df['event_time'].max() - user_df['last_event']).dt.days
user_df['activity_days'] = (user_df['last_event'] - user_df['first_event']).dt.days + 1
user_df['purchase_freq'] = user_df['num_purchases'] / user_df['activity_days']
user_df['view_freq'] = user_df['num_views'] / user_df['activity_days']
user_df['cart_freq'] = user_df['num_cart'] / user_df['activity_days']

# impute NaN recency with max, bc higher the recency, the more inactive the user is
max_recency = user_df['recency_days'].max()
user_df['recency_days'].fillna(max_recency, inplace=True)

# fill other features with 0
user_df = user_df.fillna(0)

In [7]:
# more feature engineering for clustering, categorical features
user_cat_df = df.groupby('user_id').agg(
    fav_category=('category_code', lambda x: x.mode()[0] if len(x)>0 else 'unknown'),
    fav_brand=('brand', lambda x: x.mode()[0] if len(x)>0 else 'unknown'),
    most_active_day=('day_of_week', lambda x: x.mode()[0] if len(x)>0 else 'unknown')
).reset_index()

# combine categorical features with user_df
user_df = user_df.merge(user_cat_df, on='user_id', how='left')

In [8]:
# subset
sample_size = 50000
if len(user_df) > sample_size:
    cluster_df = user_df.sample(n=sample_size, random_state=42)
else:
    cluster_df = user_df.copy()

cluster_df.head(5)

user_id  num_events  num_views  num_cart  num_purchases  \
433218  531740732           3          1         1              1   
102615  513914150           3          3         0              0   
389771  526992454           1          1         0              0   
85671   513598066           2          2         0              0   
280880  519087817           1          1         0              0   

        avg_price_viewed  unique_categories  unique_brands  \
433218        169.036667                  2              1   
102615        344.866667                  1              1   
389771        349.820000                  1              1   
85671         324.310000                  1              1   
280880         20.340000                  1              1   

                      last_event               first_event  avg_hour  \
433218 2019-10-26 06:22:25+00:00 2019-10-19 06:29:46+00:00       6.0   
102615 2019-10-12 06:50:42+00:00 2019-10-12 06:46:29+00:00       6.0   
389771 2019-10-09 20:38:50+00:00 2019-10-09 20:38:50+00:00      20.0   
85671  2019-10-07 05:39:26+00:00 2019-10-07 05:32:01+00:00       5.0   
280880 2019-10-18 12:29:46+00:00 2019-10-18 12:29:46+00:00      12.0   

        conversion_rate  recency_days  activity_days  purchase_freq  \
433218              1.0             0              7       0.142857   
102615              0.0            14              1       0.000000   
389771              0.0            16              1       0.000000   
85671               0.0            19              1       0.000000   
280880              0.0             8              1       0.000000   

        view_freq  cart_freq                       fav_category fav_brand  \
433218   0.142857   0.142857                 electronics.tablet   samsung   
102615   3.000000   0.000000             electronics.smartphone    xiaomi   
389771   1.000000   0.000000             electronics.smartphone    xiaomi   
85671    2.000000   0.000000                  computers.desktop    pulser   
280880   1.000000   0.000000  appliances.kitchen.coffee_grinder     vitek   

       most_active_day  
433218        Saturday  
102615        Saturday  
389771       Wednesday  
85671           Monday  
280880          Friday

In [9]:
# select features
selected_features = ['num_events', 'num_views', 'num_cart', 'num_purchases', 
                    'avg_price_viewed', 'unique_categories', 'unique_brands', 'avg_hour', 
                    'conversion_rate', 'recency_days', 'activity_days',
                    'purchase_freq', 'view_freq', 'cart_freq',
                    'fav_category', 'fav_brand', 'most_active_day'
                    ]
X = cluster_df[selected_features]


# make a deep copy of original feature cols
X = cluster_df[selected_features].copy()

X.head(5)

In [10]:
cat_cols = ['fav_category', 'fav_brand', 'most_active_day']
num_cols = list(set(selected_features) - set(cat_cols))

# one-hot encode categorical cols and scale numerical cols
preprocessor = ColumnTransformer(transformers=[
    ('cat', OneHotEncoder(handle_unknown='ignore'), cat_cols),
    ('num', StandardScaler(), num_cols)
])

In [15]:
def compute_kmeans(X, k):
    pipe = Pipeline(steps=[
        ('preprocessor', preprocessor),
        ('kmeans', KMeans(n_clusters=k, random_state=42))
    ])
    X_transformed = pipe['preprocessor'].fit_transform(X)
    labels = pipe['kmeans'].fit_predict(X_transformed)
    inertia = pipe['kmeans'].inertia_
    sil_score = silhouette_score(X_transformed, labels)
    return labels, inertia, sil_score, X_transformed

In [16]:
def evaluate_k(X, k_list):
    inertias = []
    sil_scores = []
    for k in k_list:
        _, inertia, sil, _ = compute_kmeans(X, k)
        inertias.append(inertia)
        sil_scores.append(sil)
    
    # print results
    for i, k in enumerate(k_list):
        print(f'k={k}: inertia={inertias[i]:.2f}, silhouette={sil_scores[i]:.3f}')
    
    df_eval = pd.DataFrame({
    'k': k_list,
    'Inertia': inertias,
    'Silhouette': sil_scores
    })

    # elbow plot
    fig_inertia = px.line(df_eval, x='k', y='Inertia', markers=True, title='Elbow Method')
    fig_inertia.show()

    # silhouette plot
    fig_sil = px.bar(df_eval, x='k', y='Silhouette', title='Silhouette Score')
    fig_sil.show()
        
    return inertias, sil_scores

k_list = list(range(2,7))
inertias, sil_scores = evaluate_k(X, k_list)

k=2: inertia=705546.44, silhouette=0.375
k=3: inertia=635277.64, silhouette=0.307
k=4: inertia=588372.83, silhouette=0.225
k=5: inertia=553011.97, silhouette=0.204
k=6: inertia=521814.58, silhouette=0.135


### Trial 1 Results Interpretation

- **Elbow Method (Inertia):** Inertia drops sharply from k = 2 to k = 3, with smaller gains after k = 3, indicating less meaningful returns for additional clusters. 
- **Silhouette Score:** Highest at k = 2, showing the most distinct clusters. However, while k = 3 is slightly less separated but the seperation still meaningful.  

**Conclusion:** k = 2 gives the clearest separation, but k = 3 allows an additional moderate cluster. We will rremove redundant features (e.g., `view_freq` derived from `num_views`, etc.) to improve cluster separation and interpretability.

In [17]:
# trial 2
# reselect features, remove 'num_views', 'num_cart', 'num_purchases', 'num_events', 'activity_days'
selected_features = [#'num_events', 'num_views', 'num_cart', 'num_purchases', 
                    'avg_price_viewed', 'unique_categories', 'unique_brands', 'avg_hour', 
                    'conversion_rate', 'recency_days', #'activity_days',
                    'purchase_freq', 'view_freq', 'cart_freq',
                    'fav_category', 'fav_brand', 'most_active_day'
                    ]
X = cluster_df[selected_features]

# make a deep copy of original feature cols
X = cluster_df[selected_features].copy()

cat_cols = ['fav_category', 'fav_brand', 'most_active_day']
num_cols = list(set(selected_features) - set(cat_cols))

# one-hot encode categorical cols and scale numerical cols
preprocessor = ColumnTransformer(transformers=[
    ('cat', OneHotEncoder(handle_unknown='ignore'), cat_cols),
    ('num', StandardScaler(), num_cols)
])

inertias, sil_scores = evaluate_k(X, k_list)

k=2: inertia=508002.18, silhouette=0.237
k=3: inertia=454400.43, silhouette=0.240
k=4: inertia=420694.12, silhouette=0.136
k=5: inertia=395643.24, silhouette=0.104
k=6: inertia=375072.41, silhouette=0.113


### Trial 2 Results Interpretation

- **Elbow Method (Inertia):** Inertia drops slightly more sharply from k = 2 to k = 3, with a slightly slower drop after k = 3, indicating less meaningful returns for additional clusters.  
- **Silhouette Score:** Highest at k = 3, higher k values reduce separation.

**Conclusion:** **k = 3** has a good balance between variance reduction and cluster clarity.


In [18]:
best_k = 3  # picked based on results above

In [19]:
labels, _, _, X_transformed = compute_kmeans(X, best_k)

# reduce to 3D for visualization
pca = PCA(n_components=3)
X_pca = pca.fit_transform(X_transformed.toarray() if hasattr(X_transformed, 'toarray') else X_transformed)

pca_df = X.copy()
pca_df['cluster'] = labels
pca_df['PCA1'] = X_pca[:,0]
pca_df['PCA2'] = X_pca[:,1]
pca_df['PCA3'] = X_pca[:,2]

fig = px.scatter_3d(pca_df, x='PCA1', y='PCA2', z='PCA3',
                    color='cluster', opacity=0.7,
                    title=f'KMeans Clusters (k={best_k})')
fig.show()

In [20]:
# add cluster labels to cluster_df
cluster_df['cluster'] = labels

# get cluster summary of numerical and categorical features
num_summary = cluster_df.groupby('cluster')[num_cols].mean().round(2)
cat_summary = cluster_df.groupby('cluster')[cat_cols].agg(lambda x: x.value_counts().index[0])
cluster_summary = pd.concat([num_summary, cat_summary], axis=1)

# get the baseline averages for comparison 
base_avg = cluster_df[num_cols].mean()

def interpret_cluster(row):
    description = []

    # purchase frequency
    if row['purchase_freq'] > base_avg['purchase_freq'] * 1.2:
        description.append("Frequent Buyers")
    elif row['purchase_freq'] < base_avg['purchase_freq'] * 0.5:
        description.append("Rare Buyers")
    else:
        description.append("Occasional Buyers")

    # browsing frequency
    if row['view_freq'] > base_avg['view_freq'] * 1.2:
        description.append("High Browsing Activity")
    elif row['view_freq'] < base_avg['view_freq'] * 0.5:
        description.append("Low Browsing Activity")
    else:
        description.append("Moderate Browsing Activity")

    # recency
    if 'recency_days' in row:
        if row['recency_days'] < base_avg['recency_days']:
            description.append("Recently Active")
        else:
            description.append("Recently Inactive")

    return ", ".join(description)

cluster_summary['char'] = cluster_summary.apply(interpret_cluster, axis=1)

# cluster description
print("\nCluster Description:")
for idx, description in cluster_summary['char'].items():
    print(f"Cluster {idx}: {description}")
print(cluster_summary.drop(columns=['char']))


Cluster Description:
Cluster 0: Frequent Buyers, Moderate Browsing Activity, Recently Inactive
Cluster 1: Occasional Buyers, High Browsing Activity, Recently Active
Cluster 2: Rare Buyers, Moderate Browsing Activity, Recently Inactive
         purchase_freq  avg_price_viewed  unique_categories  view_freq  \
cluster                                                                  
0                 1.13            357.08               1.17       0.57   
1                 0.11            288.89               3.27       1.32   
2                 0.02            373.56               1.14       1.16   

         recency_days  conversion_rate  cart_freq  unique_brands  avg_hour  \
cluster                                                                      
0               10.87             1.49       1.35           1.35     10.23   
1                6.15             0.18       0.18           4.99     11.33   
2               10.84             0.04       0.16           1.36     10.95   

  

In [21]:
for col in ['purchase_freq', 'view_freq', 'recency_days', 'avg_price_viewed']:
    fig = px.box(cluster_df, x='cluster', y=col, color='cluster', title=f"{col} Distribution by Cluster")
    fig.show()

In [22]:
# export parquets
pca_df.to_parquet("pca.parquet", index=False)
cluster_df.to_parquet("cluster_features.parquet", index=False)